Autoregressive Integrated Moving Average

ARIMA (AutoRegressive Moving Average) belongs to a class of statistical models  used for analyzing and forecasting time series data. Any ‘non-seasonal’ time series that exhibits patterns and is not a random white noise can be modeled with ARIMA models.

As we can see from the above equation, the target variable Yt is modelled as a constant plus the linear combination Lags of Y (up-to p lags) plus a linear combination of the lagged forecast errors (up-to q lags)

An ARIMA model is described using 3  hyperparameters (p, d, q):

- Autoregression: Uses the dependent relationship between an observation and some number of lagged observations. p is the order of the AR term 
-  Integrated: In order to make the time series stationary, subtracting an observation from an observation at the previous time step. q is the order of 
the MA term 
- Moving Average: Uses the dependency between an observation and a residual error from a moving average to lagged observations. d is the order of differentiation required to make the time series stationary.

# Enviroment config

In [ ]:
#@title Install packages
  !pip install --upgrade numba.np.random
  !pip install --upgrade statsmodels
  !pip install --upgrade statsmodels.api 
  !pip install --upgrade yfinance
  !pip install --upgrade pandas
  !pip install --upgrade plotly
  !pip install --upgrade pandas_datareader
  !pip install --upgrade --upgrade xgboost
  !pip install --upgrade matplotlib
  !pip install --upgrade imbalanced-learn
  !pip install --upgrade matplotlib
  !pip install --upgrade numba
  !pip install --upgrade numpy
  !pip install --upgrade scikit-learn
  !pip install --upgrade cipy
  !pip install --upgrade scipy
  !pip install --upgrade ellowbrick
  !pip install --upgrade --pre pycaret #!pip install pycaret[full]
  !pip install --upgrade threadpoolctl
  !pip install --upgrade google.colab

# Sample

In [90]:
#@title import packages
#@markdown We need to import all the correct libs to perform the models.

#import numba
import sklearn
import statsmodels
import statsmodels.api as sm
from statsmodels import regression
import yfinance as yfin
import pandas as pd 
import plotly
import plotly.express as px
import sklearn
from sklearn.cluster import KMeans
from pandas_datareader import data
import pandas_datareader
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
from pycaret import *
from pycaret.time_series import *
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.io as pio
pio.renderers.default = "colab"
from pycaret.classification import *
from sklearn import preprocessing
import pandas as pd
from sklearn.preprocessing import MinMaxScaler

In [91]:
#@title Scrap data from Wikipedia
#@markdown First, To proceed with that, we need to collect the stocks from SP 500. Through a simple web scrap, we are going to collect SP500 values  from Wikipedia page.

import pandas as pd

def returnstocks():
    table=pd.read_html('https://en.wikipedia.org/wiki/List_of_S%26P_500_companies')
    stocksdf = table[0]
    stocksdf.to_csv('S&P500-Info.csv')
    stocksdf.to_csv("S&P500-Symbols.csv", columns=['Symbol'])
    stocksdf['Symbol'] = stocksdf['Symbol'].replace('.B','', regex=True)
    return stocksdf

def eachstock():
  myList = ['^GSPC']
  for stick in returnstocks()['Symbol'].unique(): 
    myList.insert(0, stick)
  return myList

In [174]:
#@title Yahoo Finance request and beta/Alpha calculation
#@markdown For this step, we are using the component from Wikipedia, and we are going to introduce a new agent, the yahoo finance. Yahoo Finance, has hot data from https://finance.yahoo.com, and we can use these data to improve our power to decision making, regarding to create a stocks portfolio.

yfin.pdr_override() #override method from pandas_datareader by importing data as pdr
#tickers = ['ZTS', 'ZION', '^GSPC']
tickers = eachstock(); tickers.remove('BRK')

#function for receive list of stocks, source where to search and initial date/lastdate
def stockdoublebench_returns(ticker, initialdate, lastdate): #future change ticker for returnstocks()['Symbol'].unique()
    stockdouble = yfin.download(ticker, initialdate, lastdate) #data = yf.download("SPY AAPL", period="max",)
    return stockdouble['Adj Close']

#stockdoublebench_returns #run just this command to check the volatility of each one. 

def stockdoublebench_percent(ticker, initialdate, lastdate): #future change ticker for returnstocks()['Symbol'].unique()
    stockdoublepercent = yfin.download(ticker, initialdate, lastdate)
    #return stockdouble['Adj Close']] #add this line to use the graph to compare the volatility
    return stockdoublepercent['Adj Close'].pct_change()[1:]

#alpha, beta and stock
abstocks = pd.DataFrame(columns=['Alpha', 'Beta', 'stocks']) #created dataframe

def alphabetastock(df, index): #Function for generate alpha and beta from stocks
    for col in df: #for column in dataframe do
        x = sm.add_constant(df[index].values) #create a matrix using 1 and the value
        model = sm.regression.linear_model.OLS(df[col].values,x).fit() #linear regression to get values https://www.statsmodels.org/dev/generated/statsmodels.regression.linear_model.OLS.html
        abstocks.loc[len(abstocks.index)] = [model.params[0], model.params[1], col] #add each value to the dataframe
    return abstocks #model.params[0], model.params[1], col

#need to add a new line at the df for show the predicted values from each stock, and its important add the value
#from the accuracy from test as well. 

# Explore


In [ ]:
#@title Sectors grouped 
#@markdown Based on the list of the SP 500, we were able to check the principal sectors
#@markdown seeing that, we are going to check every stock
fig = px.histogram(returnstocks(), x="GICS Sector")
fig.update_layout(barmode='stack', xaxis={'categoryorder':'total descending'})
fig.show(renderer="colab")

In [ ]:
#@title SP500 index ploted
#@markdown plot the volatilty of each oone by time, can check covid and other things like ukraine war
#@markdown Changed this due to stock returns error, added missing parameters to function call

tickers = ['^GSPC']

pd.options.plotting.backend = "plotly"
stock_returns_perc = stockdoublebench_returns(tickers,'2017-01-01', '2022-01-01')

stock_returns_perc
fig = stock_returns_perc.plot()
fig.show()



[*********************100%***********************]  1 of 1 completed


# Modify


In [175]:
stockdfs = pd.DataFrame()
def datenormalization(stockdf): 
  global stockdfs
  stockdf = stockdf.groupby('Date').sum()
  stockdf = stockdf.asfreq(freq ='D'); 
  stockdfs = stockdf.ffill() #associate frequency by day to get hollidays
  stockdfs.sort_index(ascending=True, inplace=True)
  return pd.DataFrame(stockdfs)
  
obj = '' #global variable
def scaler_fit(series):
  global obj
  scaler = MinMaxScaler()
  obj = scaler.fit(series)
  return obj

def min_max_fit(series): #normalization
  scaler_fit(series)
  scaler = MinMaxScaler()
  series[list(series.columns)] = scaler.fit_transform(series)
  return series

def min_max_inverse(series, obj): #denormalization
  series[list(series.columns)] = obj.inverse_transform(series)
  return series

# Model



In [ ]:
#@title Autocorrelation

from statsmodels.graphics.tsaplots import plot_acf
fig, (ax1, ax2, ax3) = plt.subplots(3)
plot_acf(stock_returns_perc, ax=ax1)
plot_acf(stock_returns_perc.diff().dropna(), ax=ax2)
plot_acf(stock_returns_perc.diff().diff().dropna(), ax=ax3)

In [ ]:
#@title Partial-Autocorrelation



plot_pacf(stock_returns_perc.diff().dropna())

In [ ]:
#@title Finding the value of the d-parameter 
#@markdown There is no such method that can tell us how much value of d will be optimal. However, the value of differencing can be optimal till 2 so we will try our time series in both. Pandas provide this option of differencing. Let’s utilize this.

import numpy as np, pandas as pd
plt.rcParams.update({'figure.figsize':(9,7), 'figure.dpi':120})
 
# Original Series
fig, (ax1, ax2, ax3) = plt.subplots(3)
ax1.plot(stock_returns_perc); ax1.set_title('Original Series'); ax1.axes.xaxis.set_visible(False)
# 1st Differencing
ax2.plot(stock_returns_perc.diff()); ax2.set_title('1st Order Differencing'); ax2.axes.xaxis.set_visible(False)
# 2nd Differencing
ax3.plot(stock_returns_perc.diff().diff()); ax3.set_title('2nd Order Differencing')
plt.show()

#Here we can see how the time series has become stationary. 
#One thing which is noticeable here is in first-order differencing we have 
#fewer noises in the data while after 1st order there is an increase in the noise. 
#So we can select 1st order differencing for our model. We can also verify this using an autocorrelation plot. 

In [ ]:
#@title P value and new metrics based on SP500 
#@markdown Here we can see that the p-value is more than 0.05 this means our null hypothesis will be rejected and we will take this series as non-stationary. Let’s make a plot of this data 
from statsmodels.tsa.stattools import adfuller
result = adfuller(stock_returns_perc)
print('ADF Statistic: %f' % result[0])
print('p-value: %f' % result[1])
print('Critical Values:')
for key, value in result[4].items():
  print('\t%s: %.3f' % (key, value))

stock_returns_perc.plot() #Here it is visible that the data is not stationary and requires differentiation. 

In [ ]:
#@title Setup pycaret
#@markdown Setting up pycaret, fold is the number of cross fold validations. FH is the number of months to predict into the **future**

from pycaret.time_series import *

stock_returns = min_max_fit(datenormalization(stockdoublebench_returns('^GSPC', '2015-01-01', '2022-12-01')))
 #Setting up pycaret, fold is the number of cross fold validations. FH is the number of months to predict into the future
exp = setup(stock_returns, fh = 30, fold = 5, session_id = 123) 

In [ ]:
#@title Pycaret chose for you
#@markdown compcare model choose value for you
#best = exp.compare_models(turbo=False)

In [ ]:
#@title Diagnostics regarding the setup target
#@markdown Diagnostics regarding the value

exp.plot_model(plot = 'diagnostics') 

In [ ]:
#@title STL Diagnostics plot
exp.plot_model(plot="decomp_stl", data_kwargs={'seasonal_period': 30}) 

In [ ]:
 #@title Periodogram
 exp.plot_model(plot="periodogram") 

In [ ]:
#@title Plot values splited train and test
#@markdown 
exp.plot_model(plot = 'train_test_split') 

In [ ]:
 #@title Create Model
 arima = create_model('arima')

In [ ]:
#@title Visualize the Model
plot_model(arima)

In [ ]:
#@title Tuning the Model
tuned_arima = tune_model(arima)

In [ ]:
#@title Visualize the Tuned Model
plot_model(tuned_arima)

In [ ]:
#@title Blender the tuned model with model
#get a better metric between both models

blender = blend_models([arima, tuned_arima])

In [ ]:
#@title ARIMA is the best model 

final_best = exp.finalize_model(arima)

In [ ]:
#@title Predict Values using Arima for 5 days

predict_model(final_best, fh = 5)

In [ ]:
#@title Check Finalized model parameters
#@markdown Check the parameters of the model finalized.
final_best

In [ ]:
#@title Plot predicted value from finalized model
#@markdown Plot the predictions for 5 days.
plot_model(final_best, plot='forecast', data_kwargs={'fh': 5})
#exp.plot_model(estimator=finalblend) 

In [ ]:
#@title Insample based on finalized model

plot_model(arima, plot='insample')

In [ ]:
 #@title Residuals plot

 exp.plot_model(estimator=final_best, plot = 'residuals') 

In [176]:
 #@title Engineering All to Predict Stocks
 #@markdown Engineering to predict all 500 stocks
from pycaret.time_series import *

pred_unseen_deno = pd.DataFrame()
dffdstocks = pd.DataFrame()
transpredicted = pd.DataFrame()
dfstocks = pd.DataFrame()
dfstocks.iloc[0:0]

def train_and_normalize(stock, initialdate, finaldate, predictdays, predictdaysx, crossvalidation):
  global pred_unseen_deno
  global transpredicted
  stock_returns = datenormalization(stockdoublebench_returns(stock, initialdate, finaldate))
  print(stock_returns)
  exp2 = setup(min_max_fit(stock_returns[['Adj Close']]), fh = predictdays, fold = crossvalidation, session_id = 123)
  arima2 = exp2.create_model('arima')
  #pred_holdout = predict_model(arima2) 
  pred_unseen_deno = min_max_inverse(predict_model(exp2.finalize_model(arima2), fh = predictdaysx), obj)
  #if you need to see the pred_holdout value
  #pred_unseen_deno = min_max_inverse(predict_model(finalize_model(arima2), fh = predictdaysx), obj)
  transpredicted = pred_unseen_deno.T
  transpredicted['stocks'] = stock
  return transpredicted

def iterate_predicted_stocks(initialdate, finaldate, predictdays,predictdaysx, crossvalidation): 
  global dffdstocks
  global dfstocks
  for value in (abstocksna['stocks']):
    try: 
      train_and_normalize(value, initialdate, finaldate, predictdays, predictdaysx,crossvalidation) 
      dffdstocks = dffdstocks.append(transpredicted, ignore_index = True)
      dfstocks = pd.merge(dffdstocks, abstocks, on='stocks')
    except:
      continue
  return dfstocks
  #We are going to use this function to start up our algoritm to predict future values. 
#initial date, last date, predictdays(for test), predictdate for future to be used after last date, and how 
#many values fold we are going to use for cross validation.

abstocks = alphabetastock(stockdoublebench_percent(tickers, '2015-01-01', '2022-12-25'),'^GSPC')
abstocksna = abstocks.dropna()
iterate_predicted_stocks('2015-01-01', '2022-12-25', 30, 10 ,5) 

Output hidden; open in https://colab.research.google.com to view.

In [177]:
#@title sample Dataframe
dfstocks = dfstocks.drop_duplicates()
dfstocks

2022-12-24   2022-12-25   2022-12-26   2022-12-27   2022-12-28  \
0     149.278613   149.322772   147.011743   148.027418   150.205968   
1      12.708078    12.712872    12.382026    12.429975    12.933437   
2     142.845490   142.458483   142.879142   141.078720   143.754114   
3     132.320545   132.706733   130.904525   131.113710   134.492850   
4      63.093633    62.842510    62.133197    63.639935    64.595965   
..           ...          ...          ...          ...          ...   
446   109.783369   109.826675   108.430054   108.267656   111.158337   
447   129.002547   129.078345   128.159294   128.434062   128.680405   
448    48.094239    47.795584    47.209334    47.386315    48.641775   
449   145.603613   145.479053   144.088134   143.278495   145.645133   
450  3846.669678  3848.153418  3814.917641  3819.962357  3877.828219   

      2022-12-29   2022-12-30   2022-12-31   2023-01-01   2023-01-02 stocks  \
0     149.146133   149.396372   149.455252   149.514131   147.217822      A   
1      12.463539    12.612180    12.612180    12.612180    12.281334    AAL   
2     143.333455   144.359864   143.754114   143.249323   143.552198    AAP   
3     131.467715   131.258530   131.853902   132.368819   130.647067   AAPL   
4      63.939521    64.344842    63.943926    63.595879    62.802859   ACGL   
..           ...          ...          ...          ...          ...    ...   
446   109.848328   109.783369   109.848328   109.913287   108.527492    XYL   
447   128.756204   128.879375   129.012022   129.116244   128.225617    YUM   
448    49.194840    49.233555    48.768980    48.376303    47.707093   ZION   
449   145.686653   146.350972   146.164132   145.977292   144.565614    ZTS   
450  3822.336341  3845.482686  3847.856670  3849.933906  3816.994877  ^GSPC   

            Alpha      Beta  
0    4.261607e-04  1.038696  
1   -6.688356e-04  1.381072  
2   -1.236109e-04  0.884754  
3    5.519011e-04  1.209176  
4    3.796538e-04  0.931286  
..            ...       ...  
446  3.185695e-04  1.076033  
447  3.378120e-04  0.828602  
448  1.633581e-04  1.127388  
449  4.077939e-04  0.944148  
450  4.540097e-19  1.000000  

[451 rows x 13 columns]

In [12]:
#@title Save at the disk dataframe with date
import os
import datetime

Current_Date = datetime.datetime.today().strftime ('%d-%b-%Y')
dfstocks.to_csv('./Desktop/stockspred'+str(Current_Date)+'.csv', index=False, encoding='utf-8-sig')

In [186]:
last_n_column  = dfstocks.iloc[: , -4:]
last_n_column.rename(columns={ last_n_column.columns[0]: "Lastday Stock" }, inplace = True)
last_n_column

Lastday Stock stocks         Alpha      Beta
0       147.217822      A  4.261607e-04  1.038696
1        12.281334    AAL -6.688356e-04  1.381072
2       143.552198    AAP -1.236109e-04  0.884754
3       130.647067   AAPL  5.519011e-04  1.209176
4        62.802859   ACGL  3.796538e-04  0.931286
..             ...    ...           ...       ...
446     108.527492    XYL  3.185695e-04  1.076033
447     128.225617    YUM  3.378120e-04  0.828602
448      47.707093   ZION  1.633581e-04  1.127388
449     144.565614    ZTS  4.077939e-04  0.944148
450    3816.994877  ^GSPC  4.540097e-19  1.000000

[451 rows x 4 columns]

In [187]:
import plotly.express as px
fig = px.scatter(last_n_column, x='Lastday Stock', y='Beta' ,color="Beta",
                 title="Beta Variance veruss price of each Stock predicted")
fig.show()

# Assess(to-do)

In [ ]:
plot_model(tuned_arima) 

In [ ]:
plot_model(best, plot='forecast', data_kwargs={'fh': 10})

In [ ]:
plot_model(best, plot = 'insample')

In [ ]:
 exp.plot_model(estimator=final_arima, plot = 'residuals') 

In [ ]:
#need to added for to loop for all stock to get the predictons for PSO to decide what stock we will get. 

# PSO

In [ ]:
#xi(t) = xi(t) + vi(t+1)
#vi(t) = w*vi(t) + c1*rand()*Xipbest-xi(t)) + c2*rand()*Xigbest-xi(t))

#xi(t) stock price in the time t
#vi(t) stock variation (12 months)
#w stock inertia mensure by volatility index or beta
#c1+c2 usualy is a value of 4
#rand() aleatory value bettwen 0 and 1
#Xipbest the best stock price
#Xigbest the best stock price of sector

from random import uniform

def pso(stockPrice, stockVariation, w, bestPriceStock, bestStockPriceSector) :
    c1 = 1;
    c2 = 3;

    return stockPrice + w*stockVariation + c1*uniform(0,1)*(bestPriceStock-stockPrice) + c2*uniform(0,1)*(bestStockPriceSector-stockPrice);


print(pso(100.5, 5, 1, 150, 120));


143.56215303081842
